In [141]:
%matplotlib inline

import numpy as np 
import pandas as pd 
pd.set_option('display.max_rows',2200)
import matplotlib.pyplot as plt
from matplotlib import pyplot

from sklearn.linear_model import LogisticRegression
from sklearn.utils import shuffle
from sklearn.model_selection import PredefinedSplit
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.metrics import log_loss
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from sklearn.metrics import accuracy_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import NearestNeighbors, KNeighborsClassifier
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()

from xgboost import XGBClassifier
from xgboost import plot_importance

In [31]:
#Load the dataframes
df_seeds = pd.read_csv('NCAATourneySeeds.csv')
df_matches_NCAA = pd.read_csv('NCAATourneyCompactResults.csv')
df_matches_reg = pd.read_csv('RegularSeasonCompactResults.csv')

#We can choose to concatinate the two dataframes or only use one
#df_matches = pd.concat([df_matches_NCAA, df_matches_reg])
df_matches = df_matches_NCAA

In [32]:
#Display top 5 rows in the dataframe

print(df_matches_NCAA.shape)
print(df_matches_reg.shape)

print(df_seeds.head())
df_matches_NCAA.head()

(2117, 8)
(150684, 8)
   Season Seed  TeamID
0    1985  W01    1207
1    1985  W02    1210
2    1985  W03    1228
3    1985  W04    1260
4    1985  W05    1374


Season  DayNum  WTeamID  WScore  LTeamID  LScore WLoc  NumOT
0    1985     136     1116      63     1234      54    N      0
1    1985     136     1120      59     1345      58    N      0
2    1985     136     1207      68     1250      43    N      0
3    1985     136     1229      58     1425      55    N      0
4    1985     136     1242      49     1325      38    N      0

In [33]:
#Extract the numeric part of the seed (drop the regions at the beginning and the (a,b) at the end).
#Then convert the numeric string to integer
df_seeds['Seed'] = df_seeds['Seed'].str.extract('(\d+)').astype(int)
cols = ['Season', 'TeamID', 'Seed']
df_seeds = df_seeds[cols]
df_seeds.head()

/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:3: FutureWarning: currently extract(expand=None) means expand=False (return Index/Series/DataFrame) but in a future version of pandas this will be changed to expand=True (return DataFrame)
  This is separate from the ipykernel package so we can avoid doing imports until


Season  TeamID  Seed
0    1985    1207     1
1    1985    1210     2
2    1985    1228     3
3    1985    1260     4
4    1985    1374     5

In [34]:
#Drop some of the columns to make the dataframe simpler
#DayNum is the day in which the match was played
#NumOT: the number of overtime periods in the game.
#WLoc is  this identifies the "location" of the winning team. 
# ---If the winning team was the home team, this value will be "H".
# ---If the winning team was the visiting team, this value will be "A".
# ---If it was played on a neutral court, then this value will be "N".

#axis = 0 drops a row. axis = 1 drops from the columns
#inplace = True does the operation inplace, so you dont need to write df = df.drop....
df_matches.drop(labels=['DayNum', 'WLoc', 'NumOT'], inplace = True, axis=1)
print(df_matches.shape)

# Drop the matches before some year if you want, or choose 1984 to take all data
df_matches = df_matches[df_matches.Season > 1984]
print(df_matches.shape)

#Swap the second and third columns to have teams and scores next to each other for better visualisation
df_matches = df_matches[["Season","WTeamID","LTeamID", "WScore", "LScore"]]
df_matches

(2117, 5)
(2117, 5)


Season  WTeamID  LTeamID  WScore  LScore
0       1985     1116     1234      63      54
1       1985     1120     1345      59      58
2       1985     1207     1250      68      43
3       1985     1229     1425      58      55
4       1985     1242     1325      49      38
5       1985     1246     1449      66      58
6       1985     1256     1338      78      54
7       1985     1260     1233      59      58
8       1985     1314     1292      76      57
9       1985     1323     1333      79      70
10      1985     1326     1235      75      64
11      1985     1328     1299      96      83
12      1985     1374     1330      85      68
13      1985     1385     1380      83      59
14      1985     1396     1439      60      57
15      1985     1424     1361      85      80
16      1985     1104     1112      50      41
17      1985     1130     1403      55      53
18      1985     1181     1337      75      62
19      1985     1208     1455      67      59
20      1985     1210     1273      65      58
21      1985     1228     1318      76      57
22      1985     1268     1275      69      68
23      1985     1272     1335      67      55
24      1985     1276     1192      59      55
25      1985     1298     1261      78      55
26      1985     1301     1305      65      56
27      1985     1393     1177      70      65
28      1985     1412     1277      70      68
29      1985     1431     1409      79      75
30      1985     1433     1267      81      65
31      1985     1437     1173      51      49
32      1985     1120     1242      66      64
33      1985     1207     1396      63      46
34      1985     1246     1424      64      61
35      1985     1256     1326      79      67
36      1985     1260     1374      70      57
37      1985     1314     1323      60      58
38      1985     1328     1229      75      69
39      1985     1385     1116      68      65
40      1985     1104     1433      63      59
41      1985     1130     1181      74      73
42      1985     1210     1393      70      53
43      1985     1228     1208      74      58
44      1985     1268     1298      64      59
45      1985     1272     1412      67      66
46      1985     1301     1431      86      73
47      1985     1437     1276      59      55
48      1985     1207     1260      65      53
49      1985     1210     1228      61      53
50      1985     1272     1130      59      57
51      1985     1328     1256      86      84
52      1985     1301     1104      61      55
53      1985     1314     1120      62      56
54      1985     1385     1246      86      70
55      1985     1437     1268      46      43
56      1985     1207     1210      60      54
57      1985     1272     1328      63      61
58      1985     1385     1301      69      60
59      1985     1437     1314      56      44
60      1985     1207     1385      77      59
61      1985     1437     1272      52      45
62      1985     1437     1207      66      64
63      1986     1133     1431      83      65
64      1986     1177     1438      72      68
65      1986     1181     1290      85      78
66      1986     1207     1403      70      64
67      1986     1210     1265      68      53
68      1986     1242     1299      71      46
69      1986     1257     1180      93      73
70      1986     1261     1345      94      87
71      1986     1272     1123      95      63
72      1986     1277     1449      72      70
73      1986     1314     1428      84      72
74      1986     1328     1318      80      74
75      1986     1330     1452      72      64
76      1986     1396     1239      61      50
77      1986     1412     1281      66      64
78      1986     1437     1439      71      62
79      1986     1104     1462      97      80
80      1986     1114     1323      90      83
81      1986     1120     1112      73      63
82      1986     1156     1231      83      79
83      1986     1228     1193      75      51
84      198

In [6]:
#Gather the information from a team in each season.
#E.g in 2011, how many games Team 1117 won, how many lost, how many scored in the won games,
# Total of all scores in that season etc.

df_WTeams = pd.DataFrame({'GamesWon' : df_matches.groupby(["Season", "WTeamID"]).size(),
                       'WTotalScore' : df_matches.groupby(["Season", "WTeamID"])["WScore"].sum(),
                      'WScoreAvg' : df_matches.groupby(["Season", "WTeamID"])["WScore"].mean()}).reset_index()
df_WTeams = df_WTeams.rename(columns={'WTeamID':'TeamID'})

df_LTeams = pd.DataFrame({'GamesLost' : df_matches.groupby(["Season", "LTeamID"]).size(),
                       'LTotalScore' : df_matches.groupby(["Season", "LTeamID"])["LScore"].sum(),
                      'LScoreAvg' : df_matches.groupby(["Season", "LTeamID"])["LScore"].mean()}).reset_index()
df_LTeams = df_LTeams.rename(columns={'LTeamID':'TeamID'})

df_Teams = pd.merge(left=df_WTeams, right=df_LTeams, how='outer', on=['Season', 'TeamID'])
df_Teams = df_Teams.fillna(0)

df_Teams["TotalScore"] = df_Teams.WTotalScore + df_Teams.LTotalScore
df_Teams["AverageScore"] = (df_Teams.WTotalScore + df_Teams.LTotalScore)/(df_Teams.GamesWon+df_Teams.GamesLost)

df_Teams = df_Teams.round().astype('int')
df_Teams = pd.merge(left=df_seeds, right=df_Teams, how='right', on=['Season', 'TeamID'])
df_Teams = df_Teams.sort_values(by=['Season', 'Seed'])
df_Teams.head()

Season  TeamID  Seed  GamesWon  WScoreAvg  WTotalScore  GamesLost  \
0     1985    1207     1         5         67          333          1   
16    1985    1385     1         4         76          306          1   
32    1985    1328     1         3         86          257          1   
48    1985    1276     1         1         59           59          1   
1     1985    1210     2         3         65          196          1   

    LScoreAvg  LTotalScore  TotalScore  AverageScore  
0          64           64         397            66  
16         59           59         365            73  
32         61           61         318            80  
48         55           55         114            57  
1          54           54         250            62

In [35]:
# We are going to merge the matches and seeds databases.
# The seed and score difference in each match is also calculated
# First, in the seeds df, change TeamID to WTeamID and LTeamID to match with the df_matches df
# Then merge the winning teams seeds
# Then merge the losing teams seeds
# Calculate the seed and score difference in each match

df_winseeds = df_Teams.rename(columns={'TeamID':'WTeamID', 'Seed':'WSeed', 'GamesWon':'WGamesWon',
                                      'WScoreAvg':'WWScoreAvg', 'WTotalScore':'WWTotalScore',
                                     'GamesLost':'WGamesLost','LScoreAvg':'WLScoreAvg',
                                       'LTotalScore':'WLTotalScore',
                                     'AverageScore':'WAverageScore', 'TotalScore':'WTotalScore'})

df_lossseeds = df_Teams.rename(columns={'TeamID':'LTeamID', 'Seed':'LSeed', 'GamesWon':'LGamesWon',
                                      'WScoreAvg':'LWScoreAvg', 'WTotalScore':'LWTotalScore',
                                     'GamesLost':'LGamesLost','LScoreAvg':'LLScoreAvg',
                                       'LTotalScore':'LLTotalScore',
                                     'AverageScore':'LAverageScore', 'TotalScore':'LTotalScore'})

df_dummy = pd.merge(left=df_matches, right=df_winseeds, how='left', on=['Season', 'WTeamID'])
df = pd.merge(left=df_dummy, right=df_lossseeds, how='left', on=['Season', 'LTeamID'])
df['SeedDiff'] = df.WSeed - df.LSeed
df['GamesDiff'] = df.WGamesWon - df.LGamesWon
df['GamesDiff'] = df.WGamesWon - df.LGamesWon
df['ScoreDiff'] = df.WTotalScore - df.LTotalScore
df['AvgScoreDiff'] = df.WAverageScore - df.LAverageScore
df

Season  WTeamID  LTeamID  WScore  LScore  WSeed  WGamesWon  WWScoreAvg  \
0       1985     1116     1234      63      54      9          1          63   
1       1985     1120     1345      59      58     11          2          62   
2       1985     1207     1250      68      43      1          5          67   
3       1985     1229     1425      58      55      9          1          58   
4       1985     1242     1325      49      38      3          1          49   
5       1985     1246     1449      66      58     12          2          65   
6       1985     1256     1338      78      54      5          2          78   
7       1985     1260     1233      59      58      4          2          64   
8       1985     1314     1292      76      57      2          3          66   
9       1985     1323     1333      79      70      7          1          79   
10      1985     1326     1235      75      64      4          1          75   
11      1985     1328     1299      96      83      1          3          86   
12      1985     1374     1330      85      68      5          1          85   
13      1985     1385     1380      83      59      1          4          76   
14      1985     1396     1439      60      57      8          1          60   
15      1985     1424     1361      85      80      4          1          85   
16      1985     1104     1112      50      41      7          2          56   
17      1985     1130     1403      55      53     11          2          64   
18      1985     1181     1337      75      62      3          1          75   
19      1985     1208     1455      67      59      6          1          67   
20      1985     1210     1273      65      58      2          3          65   
21      1985     1228     1318      76      57      3          2          75   
22      1985     1268     1275      69      68      5          2          66   
23      1985     1272     1335      67      55      2          4          64   
24      1985     1276     1192      59      55      1          1          59   
25      1985     1298     1261      78      55     13          1          78   
26      1985     1301     1305      65      56      3          3          71   
27      1985     1393     1177      70      65      7          1          70   
28      1985     1412     1277      70      68      7          1          70   
29      1985     1431     1409      79      75     11          1          79   
30      1985     1433     1267      81      65      2          1          81   
31      1985     1437     1173      51      49      8          6          55   
32      1985     1120     1242      66      64     11          2          62   
33      1985     1207     1396      63      46      1          5          67   
34      1985     1246     1424      64      61     12          2          65   
35      1985     1256     1326      79      67      5          2          78   
36      1985     1260     1374      70      57      4          2          64   
37      1985     1314     1323      60      58      2          3          66   
38      1985     1328     1229      75      69      1          3          86   
39      1985     1385     1116      68      65      1          4          76   
40      1985     1104     1433      63      59      7          2          56   
41      1985     1130     1181      74      73     11          2          64   
42      1985     1210     1393      70      53      2          3          65   
43      1985     1228     1208      74      58      3          2          75   
44      1985     1268     1298      64      59      5          2          66   
45      1985     1272     1412      67      66      2          4          64   
46      1985     1301     1431      86      73      3          3          71   
47      1985     1437     1276      59      55      8          6          55   
48      1985     1207     1260      65      53      1          5          67   
49    

In [8]:
df_TeamsA = pd.DataFrame({ 'TeamID' : df_Teams.TeamID.unique(),
                        'NQualified' : df_Teams.groupby(["TeamID"])["Season"].size(),
                       'Champ' : df_Teams[df_Teams.GamesLost ==0].groupby(["TeamID"])["Season"].size(),
                      'AvgWon' : df_Teams.groupby(["TeamID"])["GamesWon"].mean(),
                        'AvgSeed' : df_Teams.groupby(["TeamID"])["Seed"].mean()  
                         })
df_TeamsA = df_TeamsA.fillna(0)
df_TeamsA = df_TeamsA.sort_values(by='NQualified', ascending=False)
df_TeamsA.head()

AvgSeed    AvgWon  Champ  NQualified  TeamID
TeamID                                               
1181    2.218750  2.843750    5.0          32    1299
1242    2.500000  2.500000    2.0          32    1371
1112    4.451613  1.741935    1.0          31    1301
1314    2.800000  2.933333    4.0          30    1418
1246    3.571429  2.785714    3.0          28    1258

In [121]:
df_winseeds = df_TeamsA.rename(columns={'TeamID':'WTeamID', 'AvgWon':'WAvgWon', 'Champ':'WChamp',
                                       'NQualified':'WNQualified', 'AvgSeed': 'WAvgSeed'})

df_lossseeds = df_TeamsA.rename(columns={'TeamID':'LTeamID', 'AvgWon':'LAvgWon', 'Champ':'LChamp',
                                       'NQualified':'LNQualified', 'AvgSeed': 'LAvgSeed'})

df_dummy = pd.merge(left=df_matches, right=df_winseeds, how='left', on='WTeamID')
df_dummy2 = pd.merge(left=df_dummy, right=df_lossseeds, how='left', on='LTeamID')


df_winseeds = df_seeds.rename(columns={'TeamID':'WTeamID', 'Seed':'WSeed'})
df_lossseeds = df_seeds.rename(columns={'TeamID':'LTeamID', 'Seed':'LSeed'})
df_dummy3 = pd.merge(left=df_dummy2, right=df_winseeds, how='left', on=['Season', 'WTeamID'])
df = pd.merge(left=df_dummy3, right=df_lossseeds, how='left', on=['Season', 'LTeamID'])

df['SeedDiff'] = df.WSeed - df.LSeed
df['AvgSeedDiff'] = df.WAvgSeed - df.LAvgSeed
df['ChampDiff'] = df.WChamp - df.LChamp
df['NQualifiedDiff'] = df.WNQualified - df.LNQualified
df['AvgWonDiff'] = df.WAvgWon - df.LAvgWon
df

Season  WTeamID  LTeamID  WScore  LScore   WAvgSeed   WAvgWon  WChamp  \
0       1985     1116     1234      63      54  16.000000  0.000000     0.0   
1       1985     1120     1345      59      58  11.500000  0.250000     0.0   
2       1985     1207     1250      68      43  12.000000  0.000000     0.0   
3       1985     1229     1425      58      55  13.000000  0.000000     0.0   
4       1985     1242     1325      49      38  14.200000  0.400000     0.0   
5       1985     1246     1449      66      58   9.333333  0.333333     0.0   
6       1985     1256     1338      78      54   5.250000  1.250000     0.0   
7       1985     1260     1233      59      58  16.000000  1.000000     0.0   
8       1985     1314     1292      76      57  14.666667  0.000000     0.0   
9       1985     1323     1333      79      70  13.000000  0.000000     0.0   
10      1985     1326     1235      75      64  15.000000  0.000000     0.0   
11      1985     1328     1299      96      83   6.266667  1.200000     0.0   
12      1985     1374     1330      85      68  14.400000  0.200000     0.0   
13      1985     1385     1380      83      59  13.750000  0.000000     0.0   
14      1985     1396     1439      60      57   8.571429  1.500000     0.0   
15      1985     1424     1361      85      80   6.421053  1.578947     1.0   
16      1985     1104     1112      50      41  15.000000  0.000000     0.0   
17      1985     1130     1403      55      53  15.750000  0.000000     0.0   
18      1985     1181     1337      75      62   7.800000  1.000000     0.0   
19      1985     1208     1455      67      59  15.000000  0.000000     0.0   
20      1985     1210     1273      65      58  16.000000  0.000000     0.0   
21      1985     1228     1318      76      57  14.000000  0.000000     0.0   
22      1985     1268     1275      69      68  14.000000  0.000000     0.0   
23      1985     1272     1335      67      55  15.500000  0.000000     0.0   
24      1985     1276     1192      59      55  16.000000  0.000000     0.0   
25      1985     1298     1261      78      55  15.000000  0.000000     0.0   
26      1985     1301     1305      65      56   4.451613  1.741935     1.0   
27      1985     1393     1177      70      65   9.250000  0.750000     0.0   
28      1985     1412     1277      70      68  13.142857  0.285714     0.0   
29      1985     1431     1409      79      75  13.500000  1.500000     0.0   
30      1985     1433     1267      81      65  14.800000  0.200000     0.0   
31      1985     1437     1173      51      49  16.000000  1.000000     0.0   
32      1985     1120     1242      66      64  11.500000  0.250000     0.0   
33      1985     1207     1396      63      46  12.000000  0.000000     0.0   
34      1985     1246     1424      64      61   9.333333  0.333333     0.0   
35      1985     1256     1326      79      67   5.250000  1.250000     0.0   
36      1985     1260     1374      70      57  16.000000  1.000000     0.0   
37      1985     1314     1323      60      58  14.666667  0.000000     0.0   
38      1985     1328     1229      75      69   6.266667  1.200000     0.0   
39      1985     1385     1116      68      65  13.750000  0.000000     0.0   
40      1985     1104     1433      63      59  15.000000  0.000000     0.0   
41      1985     1130     1181      74      73  15.750000  0.000000     0.0   
42      1985     1210     1393      70      53  16.000000  0.000000     0.0   
43      1985     1228     1208      74      58  14.000000  0.000000     0.0   
44      1985     1268     1298      64      59  14.000000  0.000000     0.0   
45      1985     1272     1412      67      66  15.500000  0.000000     0.0   
46      1985     1301     1431      86      73   4.451613  1.741935     1.0   
47      1985     1437     1276      59      55  16.000000  1.000000     0.0   
48      1985     1207     1260      65      53  12.000000  0.000000     0.0   
49      1985     1210     1228      61      53  16.00000

In [10]:
# Assign a win (Result = 1) to the seed and score differences
# Assign a lose (Result = 0) to the negative of the seed and score difference
# This gives us a relationship of how seed and score difference can be classified
# as win or lose. We expect higher seed difference to be more likely to win.


df_wins = df[['SeedDiff','AvgSeedDiff','ChampDiff', 'NQualifiedDiff', 'AvgWonDiff']]
df_wins['Result'] = 1

df_losses = -df[['SeedDiff','AvgSeedDiff','ChampDiff', 'NQualifiedDiff', 'AvgWonDiff']]
df_losses['Result'] = 0

data = pd.concat((df_wins, df_losses))
data.head()

/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


SeedDiff  AvgSeedDiff  ChampDiff  NQualifiedDiff  AvgWonDiff  Result
0       1.0     6.777778        0.0           -17.0   -0.388889       1
1       5.0    -3.500000        0.0            -1.0    0.250000       1
2     -15.0     7.000000        0.0             1.0    0.000000       1
3       1.0     1.000000        0.0            -1.0   -0.500000       1
4     -11.0     4.900000        0.0            -5.0   -0.300000       1

In [248]:
# The features of the model. 'Result' is the output so should subtract it
# Let's forget about ScoreDiff for now and only learn on SeedDiff

features = list(set(data.columns) - {'Result', 'ChampDiff', 'NQualifiedDiff', 'AvgSeedDiff', 'AvgWonDiff'})

X_train = data[features]
y_train = data.Result
#validation_data = data.iloc[1949:2117,:]
#X_val = validation_data[features]
features

['SeedDiff']

In [263]:
test_fold1 = np.pad([-1 for i in range(1849)], (0,2117-1849), 'constant', constant_values=(0))
test_fold = np.concatenate((test_fold1, test_fold1))
ps = PredefinedSplit(test_fold)
test_fold.shape

(4234,)

In [264]:
# Choose a model
# Choose a range for your parameter that want to GridSearch
# Train the model by fitting X and y
#Print the best parameter

logreg = LogisticRegression(penalty = 'l2', solver = 'saga')
params = {'C': np.linspace(start=0.001, stop=0.1, num=100)}
clf = GridSearchCV(logreg, params, scoring='neg_log_loss', refit=True, cv=ps)
clf.fit(X_train, y_train)
print('Best log_loss: {:.4}, with best C: {}'.format(clf.best_score_, clf.best_params_['C']))

Best log_loss: -0.5708, with best C: 0.001


In [53]:
#Now we neeed to use our trained model to predict the sample submission data 
# The format of Sample submission is SSSS_XXXX_YYYY
# S is season ID, X and Y are the two team ID's

df_sample = pd.read_csv('SampleSubmissionStage1.csv')
n_games = len(df_sample)
print(n_games)

def get_year_t1_t2(ID):
    """Return a tuple with ints `year`, `team1` and `team2`."""
    return (int(x) for x in ID.split('_'))

9112


In [54]:
df_sample2 = df_sample.copy()
df_sample2[['Season','Team1', 'Team2']] = df_sample['ID'].str.split('_',expand=True)
df_sample2 = df_sample2.drop(columns=['ID'], axis=1)
df_sample2.head()

Pred Season Team1 Team2
0   0.5   2014  1107  1110
1   0.5   2014  1107  1112
2   0.5   2014  1107  1113
3   0.5   2014  1107  1124
4   0.5   2014  1107  1140

In [55]:
df_winseeds = df_TeamsA.rename(columns={'TeamID':'Team1', 'AvgWon':'AvgWon1', 'Champ':'Champ1',
                                       'NQualified':'NQualified1', 'AvgSeed': 'AvgSeed1'})
df_lossseeds = df_TeamsA.rename(columns={'TeamID':'Team2', 'AvgWon':'AvgWon2', 'Champ':'Champ2',
                                       'NQualified':'NQualified2', 'AvgSeed': 'AvgSeed2'})

df_sample2['Team1'] = df_sample2['Team1'].astype(int)
df_sample2['Team2'] = df_sample2['Team2'].astype(int)
df_sample2['Season'] = df_sample2['Season'].astype(int)

df_dummy = pd.merge(left=df_sample2, right=df_winseeds, how='left', on=['Team1'])
df_dummy2 = pd.merge(left=df_dummy, right=df_lossseeds, how='left', on='Team2')


df_winseeds = df_seeds.rename(columns={'TeamID':'Team1', 'Seed':'Seed1'})
df_lossseeds = df_seeds.rename(columns={'TeamID':'Team2', 'Seed':'Seed2'})
df_dummy3 = pd.merge(left=df_dummy2, right=df_winseeds, how='left', on=['Season', 'Team1'])
df_test = pd.merge(left=df_dummy3, right=df_lossseeds, how='left', on=['Season', 'Team2'])

df_test['SeedDiff'] = df_test.Seed1 - df_test.Seed2
df_test['AvgSeedDiff'] = df_test.AvgSeed1 - df_test.AvgSeed2
df_test['ChampDiff'] = df_test.Champ1 - df_test.Champ2
df_test['NQualifiedDiff'] = df_test.NQualified1 - df_test.NQualified2
df_test['AvgWonDiff'] = df_test.AvgWon1 - df_test.AvgWon2
df_test.head()

Pred  Season  Team1  Team2  AvgSeed1  AvgWon1  Champ1  NQualified1  \
0   0.5    2014   1107   1110  5.533333      1.6     1.0           15   
1   0.5    2014   1107   1112  5.533333      1.6     1.0           15   
2   0.5    2014   1107   1113  5.533333      1.6     1.0           15   
3   0.5    2014   1107   1124  5.533333      1.6     1.0           15   
4   0.5    2014   1107   1140  5.533333      1.6     1.0           15   

    AvgSeed2  AvgWon2  Champ2  NQualified2  Seed1  Seed2  SeedDiff  \
0   6.250000    1.375     0.0           16     16     15         1   
1   8.100000    0.400     0.0           10     16      1        15   
2  15.000000    0.000     0.0            1     16     10         6   
3  15.000000    0.500     0.0            2     16      6        10   
4  12.333333    0.000     0.0            3     16     10         6   

   AvgSeedDiff  ChampDiff  NQualifiedDiff  AvgWonDiff  
0    -0.716667        1.0              -1       0.225  
1    -2.566667        1.0               5       1.200  
2    -9.466667        1.0              14       1.600  
3    -9.466667        1.0              13       1.100  
4    -6.800000        1.0              12       1.600

In [152]:
#X_test = df_test[['SeedDiff','AvgSeedDiff','ChampDiff', 'NQualifiedDiff', 'AvgWonDiff']]
X_test = df_test[features]
X_test.head()

ChampDiff  NQualifiedDiff  AvgSeedDiff  SeedDiff  AvgWonDiff
0        1.0              -1    -0.716667         1       0.225
1        1.0               5    -2.566667        15       1.200
2        1.0              14    -9.466667         6       1.600
3        1.0              13    -9.466667        10       1.100
4        1.0              12    -6.800000         6       1.600

In [169]:
# Based on our trained model, predict the probability of winning for the first team
# The [:,1] means we are looking for winning probability, 0 would mean for losing

preds = clf.predict_proba(X_test)[:,1]

clipped_preds = np.clip(preds, 0.05, 0.95)
df_sample.Pred = preds
df_sample


ID      Pred
0     2014_1107_1110  0.441928
1     2014_1107_1112  0.074491
2     2014_1107_1113  0.270303
3     2014_1107_1124  0.150669
4     2014_1107_1140  0.278963
5     2014_1107_1142  0.486072
6     2014_1107_1153  0.135387
7     2014_1107_1157  0.516914
8     2014_1107_1160  0.215172
9     2014_1107_1163  0.171051
10    2014_1107_1166  0.091025
11    2014_1107_1173  0.297792
12    2014_1107_1174  0.382637
13    2014_1107_1181  0.107653
14    2014_1107_1184  0.455917
15    2014_1107_1196  0.067630
16    2014_1107_1203  0.219681
17    2014_1107_1211  0.201145
18    2014_1107_1217  0.350302
19    2014_1107_1234  0.272474
20    2014_1107_1235  0.094332
21    2014_1107_1242  0.080186
22    2014_1107_1243  0.232441
23    2014_1107_1246  0.217774
24    2014_1107_1257  0.112165
25    2014_1107_1264  0.373295
26    2014_1107_1269  0.150669
27    2014_1107_1272  0.202725
28    2014_1107_1273  0.417861
29    2014_1107_1276  0.083510
30    2014_1107_1277  0.105329
31    2014_1107_1291  0.486879
32    2014_1107_1295  0.339988
33    2014_1107_1300  0.473139
34    2014_1107_1301  0.281467
35    2014_1107_1304  0.305443
36    2014_1107_1307  0.195313
37    2014_1107_1308  0.351882
38    2014_1107_1314  0.153720
39    2014_1107_1326  0.157179
40    2014_1107_1328  0.127833
41    2014_1107_1329  0.237822
42    2014_1107_1332  0.176867
43    2014_1107_1338  0.243958
44    2014_1107_1344  0.321079
45    2014_1107_1361  0.111164
46    2014_1107_1372  0.315156
47    2014_1107_1386  0.264442
48    2014_1107_1387  0.133853
49    2014_1107_1390  0.251653
50    2014_1107_1393  0.106761
51    2014_1107_1397  0.304765
52    2014_1107_1400  0.197099
53    2014_1107_1409  0.373016
54    2014_1107_1411  0.504546
55    2014_1107_1417  0.119646
56    2014_1107_1418  0.390816
57    2014_1107_1433  0.126714
58    2014_1107_1437  0.078765
59    2014_1107_1438  0.074092
60    2014_1107_1444  0.419470
61    2014_1107_1451  0.458196
62    2014_1107_1454  0.473421
63    2014_1107_1455  0.076315
64    2014_1107_1458  0.097191
65    2014_1107_1459  0.495529
66    2014_1107_1462  0.323572
67    2014_1110_1112  0.093638
68    2014_1110_1113  0.322257
69    2014_1110_1124  0.185473
70    2014_1110_1140  0.331825
71    2014_1110_1142  0.548333
72    2014_1110_1153  0.167357
73    2014_1110_1157  0.578677
74    2014_1110_1160  0.260310
75    2014_1110_1163  0.209402
76    2014_1110_1166  0.113899
77    2014_1110_1173  0.352477
78    2014_1110_1174  0.443072
79    2014_1110_1181  0.134089
80    2014_1110_1184  0.518211
81    2014_1110_1196  0.085176
82    2014_1110_1203  0.265444
83    2014_1110_1211  0.244256
84    2014_1110_1217  0.409013
85    2014_1110_1234  0.324659
86    2014_1110_1235  0.117929
87    2014_1110_1242  0.100637
88    2014_1110_1243  0.279909
89    2014_1110_1246  0.263274
90    2014_1110_1257  0.139537
91    2014_1110_1264  0.433290
92    2014_1110_1269  0.185473
93    2014_1110_1272  0.246070
94    2014_1110_1273  0.479538
95    2014_1110_1276  0.104713
96    2014_1110_1277  0.131278
97    2014_1110_1291  0.549134
98    2014_1110_1295  0.398030
99    2014_1110_1300  0.535470
100   2014_1110_1301  0.334582
101   2014_1110_1304  0.360811
102   2014_1110_1307  0.237546
103   2014_1110_1308  0.410691
104   2014_1110_1314  0.189072
105   2014_1110_1326  0.193145
106   2014_1110_1328  0.158345
107   2014_1110_1329  0.285980
108   2014_1110_1332  0.216182
109   2014_1110_1338  0.292880
110   2014_1110_1344  0.377740
111   2014_1110_1361  0.138329
112   2014_1110_1372  0.371343
113   2014_1110_1386  0.315757
114   2014_1110_1387  0.165529
115   2014_1110_1390  0.301503
116   2014_1110_1393  0.133011
117   2014_1110_1397  0.360073
118   2014_1110_1400  0.239602
119   2014_1110_1409  0.432997
120   2014_1110_1411  0.566565
121   2014_1110_1417  0.148537
122   2014_1110_1418  0.451598
123   2014_1110_1433  0.157007
124   2014_1110_1437  0.098893
125   2014_1110_1438  0.093147
126   2014_1110_1444  0.481188
127   2014_1110_1451  0.520503
128   2014_1110_145

In [170]:
#Create the file to be uploaded on Kaggle

df_sample.to_csv('submission4.csv', index=False)